# 統計モデリング概論 DSHC 2023

岩嵜 航 (Watal M. Iwasaki, PhD)<br>
東北大学 生命科学研究科 進化ゲノミクス分野 特任助教

2023-08-30 東京海上 Data Science Hill Climb<br>
https://heavywatal.github.io/slides/tokiomarine2023/

# Stanで階層ベイズモデル(HBM)

## 環境セットアップ

Google Colab の場合はインストールから:
```py
%pip install 'matplotlib>=3.1' 'seaborn>=0.11' 'statsmodels'
%pip install 'arviz>=0.12.1' 'cmdstanpy>=1.0.4'
import cmdstanpy
cmdstanpy.install_cmdstan()
```

In [ ]:
%matplotlib inline

import arviz as az
import numpy as np
import pandas as pd
import seaborn as sns
from cmdstanpy import CmdStanModel
from scipy import special, stats

rng = np.random.default_rng(seed=24601)

## 階層ベイズモデル

### データ準備


In [ ]:
sample_size = 100
mu_ind = 0.5
sd_ind = 3
z = rng.normal(mu_ind, sd_ind, size=sample_size)
p = special.expit(z)
y = rng.binomial(8, p)
mydata = {
    "N": sample_size,
    "y": y,
}
df_obs = pd.DataFrame({"z": z, "p": p, "y": y})

In [ ]:
sns.countplot(x="y", data=df_obs, color="#333")

In [ ]:
model = CmdStanModel(stan_file="stan/glmm.stan")

### MCMCサンプル

In [ ]:
fit = model.sample(mydata)

### 推定結果の要約と収束診断

In [ ]:
fit.summary()

In [ ]:
print(fit.diagnose())

### トレースプロット・事後分布確認

In [ ]:
stan_data = az.from_cmdstanpy(fit, observed_data=mydata)
az.plot_trace(stan_data)
# az.plot_posterior(stan_data)

事後分布の平均を使って予測値を描いてみる。

In [ ]:
df_p = fit.draws_pd("p")
p = np.ravel(df_p)

y = np.arange(0, 9)
count_exp = []
for y_i in y:
    freqs = stats.binom.pmf(y_i, 8, p)
    count_exp.append(sample_size * np.mean(freqs))

df_exp = pd.DataFrame({"y": y, "count": count_exp})
sns.countplot(x="y", data=df_obs, color="#333")
sns.scatterplot(x="y", y="count", data=df_exp, color="#56B4E9", s=120)

事後予測分布を描いてみる。

In [ ]:
draws = fit.draws_pd("yrep")
yrep = draws.apply(np.bincount, 1)
yrep[0:200].apply(sns.scatterplot, color="#56B4E9", alpha=0.05)
sns.scatterplot(np.bincount(df_obs["y"]), color="black")

<hr>

### ビール注文数の過分散をStanで

まずデータ生成

In [ ]:
samplesize = 300
lambda_ = 3
overdisp = 4
n_ = lambda_ / (overdisp - 1)
p_ = 1 / overdisp
X = rng.negative_binomial(n_, p_, size=samplesize)
df_beer_od = pd.DataFrame({"X": X})
data_beer_od = {"X": X, "N": samplesize}
sns.countplot(x="X", data=df_beer_od, color="#333")

Stanでモデルを記述し、コンパイルして、MCMCサンプリング

In [ ]:
model = CmdStanModel(stan_file="stan/beer-od.stan")
fit = model.sample(data_beer_od)

結果を確認

In [ ]:
fit.summary()

In [ ]:
print(fit.diagnose())

In [ ]:
stan_data = az.from_cmdstanpy(fit, observed_data=data_beer_od)

In [ ]:
az.plot_trace(stan_data)
#az.plot_posterior(stan_data)

事後予測分布を描いてみる。

In [ ]:
draws = fit.draws_pd("yrep")
yrep = draws.apply(np.bincount, 1)
yrep[0:200].apply(sns.scatterplot, color="#56B4E9", alpha=0.05)
sns.scatterplot(np.bincount(X), color="black")

In [ ]:
# pyright: reportGeneralTypeIssues=false
# pyright: reportMissingTypeStubs=false
# pyright: reportUnknownArgumentType=false
# pyright: reportUnknownMemberType=false
# pyright: reportUnknownVariableType=false